In [1]:
import sys
path2cpp_pkg = "/Users/mariusmahiout/Documents/repos/ising_core/build"
sys.path.append(path2cpp_pkg)
import ising

import os
os.chdir("/Users/mariusmahiout/Documents/repos/ising_core/python/src")
import utils as utils
import model_eval as eval
import isingfitter as fitter
import misc_plotting as plotting

os.chdir("../..")
print(os.getcwd())

import numpy as np
import plotly
from IPython.display import display, HTML

plotly.offline.init_notebook_mode()
display(HTML(
    '<script type="text/javascript" async src="https://cdnjs.cloudflare.com/ajax/libs/mathjax/2.7.1/MathJax.js?config=TeX-MML-AM_SVG"></script>'
))

/Users/mariusmahiout/Documents/repos/ising_core


In [2]:
num_units = 70
num_sims = 50_000
num_burn = 5000

In [3]:
##############
# SIMULATION #
##############

# setting up model
beta = 1.5
h = np.random.uniform(-.3 * beta, .3 * beta, num_units)
J = np.random.normal(0,  beta / np.sqrt(num_units), (num_units, num_units))
for i in range(num_units):
    J[i, i] = 0
    for j in range(i+1, num_units):
        J[j, i] = J[i, j]

true_model = ising.NeqModel(J, h)

# simulating
true_sim = true_model.simulate(int(num_sims/0.7), num_burn)

In [4]:
#train_sample, test_sample = utils.get_train_test_samples(true_sim)
train_sample = true_sim
test_sample = true_sim

# Gradient ascent

In [5]:
lr = 0.1
win_size = 10
tol_ml = 1e-6
max_steps = 3000

In [6]:
##############
# LIKELIHOOD #
##############

# setting up model
h_init = np.random.uniform(-1.5, 1.5, num_units)
J_init = np.random.normal(0,  1,  (num_units, num_units))
J_init = (J_init.T + J_init) * np.sqrt(2) / 2
np.fill_diagonal(J_init, 0)

ml_model = ising.NeqModel(J_init, h_init)

ml_fitter = fitter.NeqFitter(ml_model)
ml_fitter.TAP(true_sim)

# inference
use_llh = False
ml_fitter.maximize_likelihood(
    sample=train_sample, 
    max_steps=1000, 
    learning_rate=0.5,
    win_size = win_size,
    tolerance= tol_ml, 
    calc_llh=use_llh
)

In [7]:
ml_fitter.maximize_likelihood(
    sample=train_sample, 
    max_steps=2000, 
    learning_rate=0.1,
    win_size = win_size,
    tolerance= tol_ml, 
    calc_llh=use_llh
)

In [8]:
ml_fitter.maximize_likelihood(
    sample=train_sample, 
    max_steps=3000, 
    learning_rate=0.05,
    win_size = win_size,
    tolerance= tol_ml, 
    calc_llh=use_llh
)

In [9]:
plotting.convergence_plot(ml_fitter, plot_llh=use_llh, path="./analyses/neq_convergence/ml200.pdf")

Button(description='Save Figure', style=ButtonStyle())

In [10]:
nmf_model = ising.NeqModel(J_init, h_init)
nmf_fitter = fitter.NeqFitter(nmf_model)
nmf_fitter.naive_mean_field(train_sample)

tap_model = ising.NeqModel(J_init, h_init)
tap_fitter = fitter.NeqFitter(tap_model)
tap_fitter.TAP(train_sample)


In [11]:
ml_sim = ml_model.simulate(num_sims, num_burn)
nmf_sim = nmf_model.simulate(num_sims, num_burn)
tap_sim = tap_model.simulate(num_sims, num_burn)

In [12]:


labels = ["nMF", "TAP", "ML"]
metadata = utils.get_metadata(
    num_units=num_units,
    is_empirical_analysis=False,
    eq_inv_methods=labels,
    num_sims=num_sims,
    true_fields="uniform(-.3 * beta, .3 * beta); beta=1.5",
    true_couplings="normal(0,  beta / sqrt(num_units)); symmetric, beta=1.5",
    num_steps=max_steps,
    learning_rate=lr,
    is_converged=None,
    num_sims_ml=num_sims,
    num_burn_ml=num_burn,
)


analysis_name = "neq_test"
bin_width = 0
analysis_path = utils.get_analysis_path(analysis_name, num_units, bin_width)

layout_spec = {
    ("fields", "scatter"): (1, 1),
    ("means", "scatter"): (1, 2),
    ("couplings", "scatter"): (2, 1),
    ("dcorrs", "scatter"): (2, 2),
}

ising_eval = eval.IsingEval(
    analysis_path=analysis_path, 
    metadata=metadata,
    true_model=true_model,
    est_models=[nmf_model, tap_model, ml_model],
    true_sample=test_sample,
    est_samples=[nmf_sim, tap_sim, ml_sim],
    labels=labels,
    layout_spec=layout_spec,
)
ising_eval.generate_plots(is_pdf=True)

    'data': [{'legendgroup': 'nMF',
              'marker': {'color': 'blue', 's…